In [22]:
import agentpy as ap
import numpy as np
import math
import matplotlib.pyplot as plt
import IPython

In [23]:
class CarAgent (ap.Agent):

    def setup(self, **kwargs):
        self.state = 0
        self.speed = 0.0
        self.step_time = self.p['step time']
        self.direction = kwargs['direction']
        self.max_speed = self.model.random.uniform(
            self.p['car']['max vel range'][0],
            self.p['car']['max vel range'][1]
        )
        self.length = self.model.random.uniform(
            self.p['car']['length range'][0],
            self.p['car']['length range'][1]
        )
        self.front_min_dist = self.model.random.uniform(
           self.p['car']['min dist range'][0],
           self.p['car']['min dist range'][1]
        )

    def update_speed(self):
        front_dist = self.p['a']

        for car in self.model.cars:
            dist = self._get_front_dsit(car)

            front_dist = dist if dist != -1 else front_dist

        # Actualiza la velocidad del auto
        if front_dist < self.front_min_dist:
            self.speed = 0
            self.state = 1
        elif front_dist < 20:
            self.speed = np.maximum(self.speed - 200*self.step_time, 0)

        elif front_dist < 50:
            self.speed = np.maximum(self.speed - 80*self.step_time, 0)
        elif front_dist*2 > self.front_min_dist:
            self.speed = np.minimum(self.speed + 5*self.step_time, self.max_speed)

    def update_position(self):
        self.model.intersection.move_by(
            self,
            (self.direction[0] * self.speed, self.direction[1] * self.speed)
        )

    def _get_front_dsit(self, target):
        c1 = self.model.intersection.positions[self]
        c2 = self.model.intersection.positions[target]
        
        # Checks neighbor is in the same lane.
        dp_direction = self._dot_product(
            self.direction,
            target.direction
        )

        # Checks neighbor is in front.
        dp_place = self._dot_product(
            (
                c2[0] - c1[0],
                c2[1] - c1[1]
            ),
            self.direction
        )

        if dp_direction > 0 and dp_place > 0:
            return math.sqrt((c1[0] - c2[0])**2 + (c1[1] - c2[1])**2)

        # Invalid target.
        return -1

    def _get_traffic_light_dist(self):
        pass
    

    def _accelerate(self):
        if self.velocity < self.max_velocity:
            self.velocity += 1

    def _deaccelerate(self):
        if self.velocity > 0:
            self.velocity -= 1

    def _dot_product(self, v1, v2):
        return v1[0] * v2[0] + v1[1] * v2[1]
        

In [24]:
class TrafficModel (ap.Model):

    def setup(self):
        direction = ap.AttrIter(
            (
                ([(0, 1)] * int(self.p['car']['amount'] * self.p['density'])) +\
                ([(0, -1)] * int(self.p['car']['amount'] * (1 - self.p['density'])))
            )
        )

        # Generate car agents.
        self.cars = ap.AgentList(
            self,
            self.p["car"]["amount"],
            CarAgent,
            direction=direction
        )

        # Generate space.
        self.intersection = ap.Space(
            self,
            (self.p['a'], self.p['a']),
            torus=True
        )

        self.intersection.add_agents(self.cars, self.place_cars())

    def step(self):
        self.cars.update_position()
        self.cars.update_speed()

    def update(self):
        for i in range(self.p['car']['amount']):
            self.record(
                i,
                self.cars[i].speed
            )

    def end(self):
        self.report(
            ['crashed'],
            [self.cars[i].state for i in range(self.p['car']['amount'])]
        )

    def place_cars(self):
        # Next car's y cordenate in upstream lane.
        next_up_lane = 0.5 * self.p['a'] - self.p['b']
        # Next car's y cordenate in downstream lane.
        next_down_lane = 0.5 * self.p['a'] + self.p['b']
        # agent list index to separate car's in lanes.
        division_index = int(self.p["car"]["amount"] * self.p["density"])
        positions = []

        # Cars spwaned in upstream lane.
        for next_car in self.cars[0:division_index:]:
            positions.append(
                (
                    round(0.5 * (self.p['a'] + self.p['l']), 1),# X cordenate.
                    next_up_lane                                # Y cordenate.
                )
            )

            next_up_lane -= next_car.length + next_car.front_min_dist

        # Cars spawned in downstrem lane.
        for next_car in self.cars[division_index::]:
            positions.append(
                (
                    round(0.5 * (self.p['a'] - self.p['l']), 1),# X cordenate.
                    next_down_lane                              # Y cordenate.
                )
            )

            next_down_lane += next_car.length + next_car.front_min_dist

        return positions

In [25]:
def animation_plot_single(m, ax):    
    ax.set_title(f"Avenida t={m.t*m.p['step time']:.2f}")
    
    # colors = ["green", "yellow", "red"]
    
    # pos_s1 = m.avenue.positions[m.semaphores[0]]    
    # ax.scatter(*pos_s1, s=20, c=colors[m.semaphores[0].state])
    
    # pos_s2 = m.avenue.positions[m.semaphores[1]]    
    # ax.scatter(*pos_s2, s=20, c=colors[m.semaphores[1].state])
    
    ax.set_xlim(0, m.intersection.shape[0])
    ax.set_ylim(0, m.intersection.shape[1])    
    
    for car in m.cars:
        pos_c = m.intersection.positions[car]    
        ax.scatter(*pos_c, s=20, c="black")
    
    ax.set_axis_off()
    ax.set_aspect('equal', 'box')
        
def animation_plot(m, p):    
    fig = plt.figure(figsize=(10, 10))
    ax = fig.add_subplot(111)
    animation = ap.animate(m(p), fig, ax, animation_plot_single)
    return IPython.display.HTML(animation.to_jshtml(fps=20))

In [26]:
param = {
        "car": {
            "amount": 8,
            "length range": (1.8, 2.3),
            "max vel range": (10.0, 16.67),
            "min dist range": (3.0, 5.0)
        },
        'a': 1000,
        'step time': 0.1,
        'b': 5,
        'l': 3.6,
        "density": 0.5,
        'steps': 1000
    }

In [27]:
model = TrafficModel(param)
result = model.run()

Completed: 1000 steps
Run time: 0:00:01.178282
Simulation finished


In [29]:
animation_plot(TrafficModel, param)

In [31]:
print(result.reporters['crashed'][0])

[1, 0, 0, 0, 0, 0, 0, 0]
